This cell installs the `coinmetrics-api-client` library, which is needed to interact with the CoinMetrics API.

In [2]:
!pip install coinmetrics-api-client -q

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 52.0/52.0 kB 2.9 MB/s eta 0:00:00


This cell initializes the CoinMetrics API client. It retrieves the API key from Colab secrets and then creates a client object. It also fetches the list of all assets and filters for assets containing "Canton".

In [3]:
from coinmetrics.api_client import CoinMetricsClient
from google.colab import userdata
from coinmetrics.api_client import CoinMetricsClient
import os
import polars as pl
from datetime import timedelta, datetime
import datetime as dt
import requests
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio

api_key = userdata.get('api_key')

client = CoinMetricsClient(api_key)

assets_df = client.reference_data_assets().to_dataframe().set_index('asset')
canton_assets = assets_df[assets_df['full_name'].str.contains("canton", case=False)]
display(canton_assets)

full_name
asset             
cc     Canton Coin

This cell retrieves the available asset metrics for Canton Coin (`cc`) and displays them. This allows us to see what data is available for this asset.

In [4]:
ref = client.reference_data_asset_metrics().to_dataframe()
asset_metrics = client.catalog_asset_metrics_v2(assets='cc').to_dataframe().merge(ref).set_index('metric')
asset_metrics.loc[:, ['frequency','min_time', 'max_time'] + list(ref.columns)[1:]]

frequency                  min_time  \
metric                                                 
AdrBal1in100KCnt        1d 2024-06-24 00:00:00+00:00   
AdrBal1in100MCnt        1d 2024-06-24 00:00:00+00:00   
AdrBal1in10BCnt         1d 2024-06-24 00:00:00+00:00   
AdrBal1in10KCnt         1d 2024-06-24 00:00:00+00:00   
AdrBal1in10MCnt         1d 2024-06-24 00:00:00+00:00   
...                    ...                       ...   
VelCur1yr               1d 2024-06-26 00:00:00+00:00   
VelCurAdj1yr            1d 2024-06-26 00:00:00+00:00   
VtyDayRet180d           1d 2024-12-21 00:00:00+00:00   
VtyDayRet30d            1d 2024-07-24 00:00:00+00:00   
VtyDayRet60d            1d 2024-08-23 00:00:00+00:00   

                                  max_time  \
metric                                       
AdrBal1in100KCnt 2025-07-28 00:00:00+00:00   
AdrBal1in100MCnt 2025-07-28 00:00:00+00:00   
AdrBal1in10BCnt  2025-07-28 00:00:00+00:00   
AdrBal1in10KCnt  2025-07-28 00:00:00+00:00   
AdrBal1in10MCnt  2025-07-28 00:00:00+00:00   
...                                    ...   
VelCur1yr        2025-07-28 00:00:00+00:00   
VelCurAdj1yr     2025-07-28 00:00:00+00:00   
VtyDayRet180d    2025-07-28 00:00:00+00:00   
VtyDayRet30d     2025-07-28 00:00:00+00:00   
VtyDayRet60d     2025-07-28 00:00:00+00:00   

                                                          full_name  \
metric                                                                
AdrBal1in100KCnt  Addresses, with balance, greater than 1in100K,...   
AdrBal1in100MCnt  Addresses, with balance, greater than 1in100M,...   
AdrBal1in10BCnt   Addresses, with balance, greater than 1in10B, ...   
AdrBal1in10KCnt   Addresses, with balance, greater than 1in10K, ...   
AdrBal1in10MCnt   Addresses, with balance, greater than 1in10M, ...   
...                                                             ...   
VelCur1yr                             Velocity, current supply, 1yr   
VelCurAdj1yr                Velocity, current supply, adjusted, 1yr   
VtyDayRet180d                       Volatility, daily returns, 180d   
VtyDayRet30d                         Volatility, daily returns, 30d   
VtyDayRet60d                         Volatility, daily returns, 60d   

                                                        description  \
metric                                                                
AdrBal1in100KCnt  The sum count of unique addresses holding at l...   
AdrBal1in100MCnt  The sum count of unique addresses holding at l...   
AdrBal1in10BCnt   The sum count of unique addresses holding at l...   
AdrBal1in10KCnt   The sum count of unique addresses holding at l...   
AdrBal1in10MCnt   The sum count of unique addresses holding at l...   
...                                                             ...   
VelCur1yr         The ratio of the value transferred (i.e., the ...   
VelCurAdj1yr      The ratio of the adjusted value transferred (i...   
VtyDayRet180d     The 180D volatility, measured as the standard ...   
VtyDayRet30d      The 30D volatility, measured as the standard d...   
VtyDayRet60d      The 60D volatility, measured as the standard d...   

                       product      category subcategory           unit  \
metric                                                                    
AdrBal1in100KCnt  Network Data     Addresses     Balance      Addresses   
AdrBal1in100MCnt  Network Data     Addresses     Balance      Addresses   
AdrBal1in10BCnt   Network Data     Addresses     Balance      Addresses   
AdrBal1in10KCnt   Network Data     Addresses     Balance      Addresses   
AdrBal1in10MCnt   Network Data     Addresses     Balance      Addresses   
...                        ...           ...         ...            ...   
VelCur1yr         Network Data  Transactions    Velocity  Dimensionless   
VelCurAdj1yr      Network Data  Transactions    Velocity  Dimensionless   
VtyDayRet180d     Network Data        Market  Volatility  Dimensionless   
VtyDayRet30d    

This cell fetches the time series data for several address-related metrics for Canton Coin since May 1, 2025.

In [164]:
address_metrics = [
    'AdrBalCnt',
    'AdrBal1in100KCnt',
    'AdrBal1in100MCnt',
    'AdrBal1in10BCnt',
    'AdrBal1in10KCnt',
    'AdrBal1in10MCnt'
]

address_metrics_df = client.get_asset_metrics(
    assets=['cc'],
    metrics=address_metrics,
    start_time="2025-05-01"
).to_dataframe()

address_metrics_df

asset                      time  AdrBal1in100KCnt  AdrBal1in100MCnt  \
0     cc 2025-05-01 00:00:00+00:00               132               228   
1     cc 2025-05-02 00:00:00+00:00               132               230   
2     cc 2025-05-03 00:00:00+00:00               134               233   
3     cc 2025-05-04 00:00:00+00:00               134               233   
4     cc 2025-05-05 00:00:00+00:00               135               237   
..   ...                       ...               ...               ...   
84    cc 2025-07-24 00:00:00+00:00               259               701   
85    cc 2025-07-25 00:00:00+00:00               261               781   
86    cc 2025-07-26 00:00:00+00:00               261               784   
87    cc 2025-07-27 00:00:00+00:00               261               785   
88    cc 2025-07-28 00:00:00+00:00               264               789   

    AdrBal1in10BCnt  AdrBal1in10KCnt  AdrBal1in10MCnt  AdrBalCnt  
0               231               88              221        249  
1               233               90              224        251  
2               236               91              227        254  
3               236               91              226        254  
4               240               92              230        258  
..              ...              ...              ...        ...  
84              740              132              671        828  
85              922              132              758        965  
86              926              133              751        969  
87              928              132              650        969  
88              933              131              653        974  

[89 rows x 8 columns]

This cell creates a line plot of the address-related metrics fetched in the previous cell. It melts the dataframe to have a 'metric' and 'value' column, and then uses the 'metric' column to color the lines.

In [165]:
import plotly.express as px

# Melt the dataframe to have a 'metric' and 'value' column
df_melted = address_metrics_df.melt(id_vars=['time', 'asset'], var_name='metric', value_name='value')

# Create the line plot
fig = px.line(
    df_melted,
    x='time',
    y='value',
    color='metric',
    title='Number of Canton Coin Addresses with Balance > X'
)
fig.show()

Let's check the catalog for Atlas

In [139]:
blockchain_accounts_df = client.catalog_blockchain_accounts_v2().to_dataframe().set_index('asset')
blockchain_accounts_df.loc['cc']

min_time        2024-06-26 00:19:05.995464+00:00
max_time        2025-07-29 04:48:02.743589+00:00
experimental                                <NA>
Name: cc, dtype: object

This cell defines a sample account address that will be used in the following cells.

In [140]:
sample = "CoinMetrics-validator-1::1220b6cf34a2c8937dc72403e7a8b57c80049be8aff3e5e2d992063460bdc8636466"

This cell retrieves the latest details of an account, including the current balance

In [141]:
current_balance = client.get_list_of_accounts_v2(accounts=sample, asset='cc').to_dataframe(dataframe_type='polars')
current_balance

shape: (1, 12)
┌────────────┬─────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ account    ┆ type    ┆ creation_ ┆ creation_ ┆ … ┆ n_credits ┆ last_chai ┆ last_debi ┆ last_cred │
│ ---        ┆ ---     ┆ height    ┆ block_has ┆   ┆ ---       ┆ n_sequenc ┆ t_height  ┆ it_height │
│ str        ┆ str     ┆ ---       ┆ h         ┆   ┆ i64       ┆ e_number  ┆ ---       ┆ ---       │
│            ┆         ┆ i64       ┆ ---       ┆   ┆           ┆ ---       ┆ i64       ┆ i64       │
│            ┆         ┆           ┆ str       ┆   ┆           ┆ i64       ┆           ┆           │
╞════════════╪═════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ CoinMetric ┆ ACCOUNT ┆ 8551660   ┆ 12209e367 ┆ … ┆ 96636     ┆ 101440560 ┆ 23618471  ┆ 23618471  │
│ s-validato ┆         ┆           ┆ 6d5164ba1 ┆   ┆           ┆ 526524423 ┆           ┆           │
│ r-1::1220b ┆         ┆           ┆ 75f69a5bf ┆   ┆           ┆           ┆           ┆           │
│ …          ┆         ┆           ┆ bbe…      ┆   ┆           ┆           ┆           ┆           │
└────────────┴─────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

This cell creates a big number visualization of the current balance of the sample account. It displays the balance in millions of CC.

In [142]:
import plotly.graph_objects as go

# Extract the balance from the dataframe
balance = current_balance['balance'][0]

fig = go.Figure(go.Indicator(
    mode = "number",
    value = balance / 1000000,
    number = {'prefix': "CC (M)", 'valueformat': '.2f'},
    title = f"Current CC Balance for account<br><span style='font-size:0.8em;color:gray'>{sample}</span>",
    domain = {'x': [0, 1], 'y': [0, 1]}
))

fig.update_layout(
    font=dict(
        size=40,
    ),
)


fig.show()

This cell fetches the balance updates for the sample account since May 1, 2025.

In [143]:
bu = client.get_list_of_balance_updates_for_account_v2(
    asset='cc',
    account=sample,
    include_sub_accounts=True,
    include_counterparties=True,
    start_time='2025-05-01',
    page_size=10000
).parallel(time_increment=timedelta(days=1)).to_list()
df = pl.DataFrame(bu, infer_schema_length=10000)

Converting to List: 100%|██████████| 90/90 [00:30<00:00,  2.96it/s]


This cell casts the columns of the `df` dataframe to their appropriate integer, float, and datetime types. This is necessary for performing calculations and plotting. (The fact this is not done automatically is a bug currently under investigation.)

In [144]:
integer_columns = [
    'chain_sequence_number',
    'account_creation_height',
    'transaction_sequence_number',
    'n_debits',
    'n_credits',
    'height',
    'previous_debit_height',
    'previous_credit_height',
    'previous_chain_sequence_number'
]

float_columns = [
    'change',
    'previous_balance',
    'new_balance',
    'credit',
    'total_received',
    'total_sent'
]

df = df.with_columns(
    [pl.col(c).cast(pl.Int64) for c in integer_columns] +
    [pl.col(c).cast(pl.Float64) for c in float_columns] +
    [pl.col('consensus_time').str.to_datetime()]
)

df.head()

shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ chain_seq ┆ account   ┆ account_c ┆ change    ┆ … ┆ previous_ ┆ previous_ ┆ txid      ┆ sub_acco │
│ uence_num ┆ ---       ┆ reation_h ┆ ---       ┆   ┆ credit_he ┆ chain_seq ┆ ---       ┆ unt      │
│ ber       ┆ str       ┆ eight     ┆ f64       ┆   ┆ ight      ┆ uence_num ┆ str       ┆ ---      │
│ ---       ┆           ┆ ---       ┆           ┆   ┆ ---       ┆ ber       ┆           ┆ struct[1 │
│ i64       ┆           ┆ i64       ┆           ┆   ┆ i64       ┆ ---       ┆           ┆ 1]       │
│           ┆           ┆           ┆           ┆   ┆           ┆ i64       ┆           ┆          │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 458895308 ┆ CoinMetri ┆ 8551660   ┆ 92.220691 ┆ … ┆ 10684130  ┆ 458879889 ┆ 1220d56b4 ┆ null     │
│ 29471744  ┆ cs-valida ┆           ┆           ┆   ┆           ┆ 36212482  ┆ 979e294a0 ┆          │
│           ┆ tor-1::12 ┆           ┆           ┆   ┆           ┆           ┆ 7009d6fd3 ┆          │
│           ┆ 20b…      ┆           ┆           ┆   ┆           ┆           ┆ e6d…      ┆          │
│ 458895308 ┆ FEES      ┆ 10344     ┆ 0.922207  ┆ … ┆ 10684485  ┆ 458895136 ┆ 1220d56b4 ┆ {"TRANSF │
│ 29471745  ┆           ┆           ┆           ┆   ┆           ┆ 49602567  ┆ 979e294a0 ┆ ER_FEE", │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 7009d6fd3 ┆ "0","0.9 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ e6d…      ┆ 222069…  │
│ 458895308 ┆ FEES      ┆ 10344     ┆ 0.6       ┆ … ┆ 10684489  ┆ 458895308 ┆ 1220d56b4 ┆ {"CREATE │
│ 29471746  ┆           ┆           ┆           ┆   ┆           ┆ 29471745  ┆ 979e294a0 ┆ _FEE","0 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 7009d6fd3 ┆ ","0.6", │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ e6d…      ┆ "99252…  │
│ 458895308 ┆ Cumberlan ┆ 4150416   ┆ 283548.00 ┆ … ┆ 10684466  ┆ 458894320 ┆ 1220d56b4 ┆ null     │
│ 29471747  ┆ d-GasStat ┆           ┆ 8779      ┆   ┆           ┆ 45223944  ┆ 979e294a0 ┆          │
│           ┆ ion-1::12 ┆           ┆           ┆   ┆           ┆           ┆ 7009d6fd3 ┆          │
│           ┆ 209…      ┆           ┆           ┆   ┆           ┆           ┆ e6d…      ┆          │
│ 458895308 ┆ FEES      ┆ 10344     ┆ 0.6       ┆ … ┆ 10684489  ┆ 458895308 ┆ 1220d56b4 ┆ {"SENDER │
│ 29471748  ┆           ┆           ┆           ┆   ┆           ┆ 29471746  ┆ 979e294a0 ┆ _CHANGE_ │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 7009d6fd3 ┆ FEE","0" │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ e6d…      ┆ ,"0.6"…  │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

This cell unnests the `sub_account` column and renames some of the columns to be more descriptive (and not clash with the unnnested ones).

In [145]:
df_details = df.rename({'previous_balance':'account_previous_balance',
                        'new_balance':'account_new_balance',
                        'n_debits':'account_n_debits',
                        'n_credits': 'account_n_credits',
                        'previous_credit_height': 'account_previous_credit_height',
                        'previous_debit_height':'account_previous_debit_height',
                        'previous_chain_sequence_number': 'account_previous_chain_sequence_number',
                        'total_received':'account_total_received',
                        'total_sent':'account_total_sent'}
                      ).unnest('sub_account')
df_details.to_pandas()

chain_sequence_number  \
0           45889530829471744   
1           45889530829471745   
2           45889530829471746   
3           45889530829471747   
4           45889530829471748   
...                       ...   
725843     101440560526524423   
725844     101440560526524424   
725845     101440560526524425   
725846     101440560526524426   
725847     101440560526524427   

                                                  account  \
0       CoinMetrics-validator-1::1220b6cf34a2c8937dc72...   
1                                                    FEES   
2                                                    FEES   
3       Cumberland-GasStation-1::1220987fe52357fc17dc0...   
4                                                    FEES   
...                                                   ...   
725843  CoinMetrics-validator-1::1220b6cf34a2c8937dc72...   
725844                                               FEES   
725845                                               FEES   
725846                                               FEES   
725847                                           ISSUANCE   

        account_creation_height         change  account_previous_balance  \
0                       8551660      92.220691              2.148357e+06   
1                         10344       0.922207              0.000000e+00   
2                         10344       0.600000              9.222069e-01   
3                       4150416  283548.008779              2.836424e+05   
4                         10344       0.600000              1.522207e+00   
...                         ...            ...                       ...   
725843                  8551660   -5842.153404              1.024745e+07   
725844                    10344      -0.002319              1.302319e+00   
725845                    10344      -1.200000              1.300000e+00   
725846                    10344      -0.100000              1.000000e-01   
725847                    10344       1.302319             -2.883062e+10   

        account_new_balance  transaction_sequence_number  account_n_debits  \
0              2.148449e+06                            0             10506   
1              9.222069e-01                            0           8855487   
2              1.522207e+00                            0           8855487   
3              5.671904e+05                            0            263445   
4              2.122207e+00                            0           8855487   
...                     ...                          ...               ...   
725843         1.024160e+07                            1             90567   
725844         1.300000e+00                            2          35878774   
725845         1.000000e-01                            2          35878775   
725846         0.000000e+00                            2          35878776   
725847        -2.883062e+10                            2           7374220   

        account_n_credits                                         block_hash  \
0                   13537  1220d56b4979e294a07009d6fd3e6db2663f920d422b5f...   
1                10130314  1220d56b4979e294a07009d6fd3e6db2663f920d422b5f...   
2                10130315  1220d56b4979e294a07009d6fd3e6db2663f920d422b5f...   
3                  480354  1220d56b4979e294a07009d6fd3e6db2663f920d422b5f...   
4                10130316  1220d56b4979e294a07009d6fd3e6db2663f920d422b5f...   
...                   ...                                                ...   
725843              96636  122084462be9150f221d7cbab468c7e3fc6252f61bca87...   
725844           48409514  122084462be9150f221d7cbab468c7e3fc6252f61bca87...   
725845           48409514  122084462be9150f221d7cbab468c7e3fc6252f61bca87...   
725846           48409514  122084462be9150f221d7cbab468c7e3fc6252f61bca87...   
725847           11478119  122084462be9150f221d7cbab468c7e3fc6252f61bca87...   

        ...      previous_balance          new_balance  n_debits  n

This cell filters the balance updates for the sample account and creates a line plot of the balance over time.

In [193]:
cm_balance = (df_details
              .filter(pl.col('account') == sample)
              .sort("chain_sequence_number")
              .group_by("consensus_time", maintain_order=True)
              .agg(pl.all().last())
              .rename({'account_new_balance':'balance', 'consensus_time':'time'})
)

bot = px.line(cm_balance, x='time', y='balance', hover_name='account')
bot

This cell removes negative changes from the 'FEES' account to exclude fee payments from the analysis.

In [147]:
balance_reasons = df_details.remove((pl.col("account") == "FEES") & (pl.col("change") <0))

This cell groups the balance reasons by transaction ID, account, and sub-account, and aggregates the change, chain sequence number, new balance, and consensus time.

In [148]:
balance_reasons = balance_reasons.group_by('txid', 'account', 'sub_account', maintain_order=True).agg(pl.col('change').sum(),
                                                                                                      pl.col('chain_sequence_number').first(),
                                                                                                      pl.col('new_balance').last(),
                                                                                                      pl.col('account_new_balance').last(),
                                                                                                      pl.col('consensus_time').first())

This cell creates a new column `balance_update_reason_amt` which is either the new balance (for 'LOCKED' sub-accounts) or the change in balance.

In [149]:
balance_reasons = balance_reasons.with_columns(pl.when(pl.col('sub_account') == 'LOCKED')
                                               .then(pl.col('new_balance'))
                                              .otherwise(pl.col('change'))
                                              .alias('balance_update_reason_amt'))

This cell filters for new issuance transactions and pivots the data to have separate columns for each sub-account type.

In [150]:
new_issuance = balance_reasons.filter((pl.col('account') == 'ISSUANCE') & (pl.col('change') < 0))
new_issuance = new_issuance.with_columns(pl.col('balance_update_reason_amt').cast(pl.Float64).abs())
new_issuance = new_issuance.pivot(on='sub_account', index=['account', 'txid'], values='balance_update_reason_amt')

This cell filters for fee transactions and pivots the data to have separate columns for each sub-account type.

In [151]:
fees = balance_reasons.filter((pl.col('account') == 'FEES'))
fees = fees.with_columns(pl.col('balance_update_reason_amt').cast(pl.Float64).abs())
fees = fees.pivot(on='sub_account', index=['account', 'txid'], values='balance_update_reason_amt')

This cell joins the `balance_reasons` dataframe with the `new_issuance` dataframe to add information about new issuance to each transaction.

In [152]:
balance_reasons = balance_reasons.filter((pl.col('account') == sample))
balance_reasons = balance_reasons.join(new_issuance, how='left', on='txid')

This cell joins the `balance_reasons` dataframe with the `fees` dataframe to add information about fees to each transaction.

In [153]:
balance_reasons = balance_reasons.join(fees, how='left', on='txid', suffix='_fees')

This cell casts the `new_balance` column to a float type.

In [154]:
balance_reasons = balance_reasons.with_columns(pl.col('new_balance').cast(pl.Float64))
balance_reasons

shape: (80_072, 21)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ txid      ┆ account   ┆ sub_accou ┆ change    ┆ … ┆ SENDER_CH ┆ LOCKING_F ┆ HOLDING_F ┆ BUY_MEMB │
│ ---       ┆ ---       ┆ nt        ┆ ---       ┆   ┆ ANGE_FEE  ┆ EE        ┆ EES       ┆ ER_TRAFF │
│ str       ┆ str       ┆ ---       ┆ f64       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ IC       │
│           ┆           ┆ str       ┆           ┆   ┆ f64       ┆ f64       ┆ f64       ┆ ---      │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ f64      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 1220d56b4 ┆ CoinMetri ┆ null      ┆ 0.0       ┆ … ┆ 0.6       ┆ 0.1       ┆ 0.000381  ┆ null     │
│ 979e294a0 ┆ cs-valida ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 7009d6fd3 ┆ tor-1::12 ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ e6d…      ┆ 20b…      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 1220d56b4 ┆ CoinMetri ┆ LOCKED    ┆ 90.458055 ┆ … ┆ 0.6       ┆ 0.1       ┆ 0.000381  ┆ null     │
│ 979e294a0 ┆ cs-valida ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 7009d6fd3 ┆ tor-1::12 ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ e6d…      ┆ 20b…      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 122016323 ┆ CoinMetri ┆ null      ┆ 1537.8054 ┆ … ┆ 0.6       ┆ null      ┆ 0.000381  ┆ null     │
│ 79c3c441f ┆ cs-valida ┆           ┆ 17        ┆   ┆           ┆           ┆           ┆          │
│ b70c6cb6c ┆ tor-1::12 ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 897…      ┆ 20b…      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 1220ca97c ┆ CoinMetri ┆ null      ┆ 0.0       ┆ … ┆ 0.6       ┆ 0.1       ┆ 0.000381  ┆ null     │
│ 5433336ec ┆ cs-valida ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ d108c714a ┆ tor-1::12 ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 9af…      ┆ 20b…      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 1220ca97c ┆ CoinMetri ┆ LOCKED    ┆ 84.737179 ┆ … ┆ 0.6       ┆ 0.1       ┆ 0.000381  ┆ null     │
│ 5433336ec ┆ cs-valida ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ d108c714a ┆ tor-1::12 ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 9af…      ┆ 20b…      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ …         ┆ …         ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ 1220ddeff ┆ CoinMetri ┆ null      ┆ 0.0       ┆ … ┆ null      ┆ 0.1       ┆ 0.000381  ┆ null     │
│ 62c651636 ┆ cs-valida ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ d8ba8d776 ┆ tor-1::12 ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 59f…      ┆ 20b…      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 1220c21ca ┆ CoinMetri ┆ LOCKED    ┆ -1.711157 ┆ … ┆ null      ┆ 0.2       ┆ 0.000381  ┆ null     │
│ bbb5c01f6 ┆ cs-valida ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 394d8c6c5 ┆ tor-1::12 ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 5c9…      ┆ 20b…      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 1220c21ca ┆ CoinMetri ┆ null      ┆ 0.0       ┆ … ┆ null      ┆ 0.2       ┆ 0.000381  ┆ null     │
│ bbb5c01f6 ┆ cs-valida ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 394d8c6c5 ┆ tor-1::12 ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 5c9…      ┆ 20b…      ┆           ┆    

This cell filters the balance updates for the first 4 days of May 2025.

In [155]:
import datetime as dt

act_balance_updates = (balance_reasons
                       .group_by('consensus_time', maintain_order=True)
                       .agg(pl.col('change').first(), pl.col('account_new_balance').last())
                       .filter(pl.col('consensus_time') < pl.lit(datetime(2025, 5, 5, tzinfo=dt.timezone.utc))))
act_balance_updates

shape: (1_127, 3)
┌────────────────────────────────┬─────────────┬─────────────────────┐
│ consensus_time                 ┆ change      ┆ account_new_balance │
│ ---                            ┆ ---         ┆ ---                 │
│ datetime[μs, UTC]              ┆ f64         ┆ f64                 │
╞════════════════════════════════╪═════════════╪═════════════════════╡
│ 2025-05-01 00:04:12.025061 UTC ┆ 0.0         ┆ 2.1519e6            │
│ 2025-05-01 00:05:01.503673 UTC ┆ 1537.805417 ┆ 2.1500e6            │
│ 2025-05-01 00:14:28.202449 UTC ┆ 0.0         ┆ 2.1536e6            │
│ 2025-05-01 00:15:24.363089 UTC ┆ 1619.4944   ┆ 2.1517e6            │
│ 2025-05-01 00:24:08.459979 UTC ┆ 0.0         ┆ 2.1554e6            │
│ …                              ┆ …           ┆ …                   │
│ 2025-05-04 23:34:17.888715 UTC ┆ 0.0         ┆ 3.0828e6            │
│ 2025-05-04 23:38:40.776449 UTC ┆ 1597.910635 ┆ 3.0811e6            │
│ 2025-05-04 23:44:43.397745 UTC ┆ 0.0         ┆ 3.0846e6            │
│ 2025-05-04 23:50:18.599727 UTC ┆ 1598.12359  ┆ 3.0828e6            │
│ 2025-05-04 23:54:26.071846 UTC ┆ 4.5475e-13  ┆ 3.0863e6            │
└────────────────────────────────┴─────────────┴─────────────────────┘

This cell creates a plot of the balance updates, with the balance change on the left y-axis and the balance over time on the right y-axis.

In [156]:
fig_bu = make_subplots(specs=[[{"secondary_y":True}]], )
fig_bu.add_trace(
    go.Scatter(
        x=act_balance_updates['consensus_time'],
        y=act_balance_updates['change'],
        mode='markers',
        name='Balance Change'
    ), secondary_y=False
)
fig_bu.add_trace(
    go.Scatter(
        x=act_balance_updates['consensus_time'],
        y=act_balance_updates['account_new_balance'],
        mode='lines',
        name='Balance over Time'
    ),secondary_y=True
)
fig_bu.update_layout(title_text='{}'.format(f"Balance Updates for {sample}").upper())

fig_bu

This cell filters for 'LOCKED' sub-accounts and creates a plot of the total amount locked over time.

In [157]:
locked = balance_reasons.filter(pl.col('sub_account') == 'LOCKED')

fig_locked = make_subplots(specs=[[{"secondary_y":True}]], )
fig_locked.add_trace(go.Scatter(
    x=locked['consensus_time'],
    y=locked['new_balance'],
    mode='lines',
    name='Total Amount Locked'
))

fig_locked.update_layout(title_text='{}'.format(f"Total Amount Locked for {sample}").upper())
fig_locked

This cell separates the rewards and fees columns into two separate lists. It then groups the data by day and calculates the daily sum of rewards and fees.

In [158]:
rewards_fees_columns = balance_reasons.columns
rewards_columns = ['SUPER_VALIDATOR_REWARD', 'VALIDATOR_LIVENESS', 'VALIDATOR_REWARD', 'UNFEATURED_APP_REWARD', 'VALIDATOR_FAUCET', 'FEATURED_APP_REWARD']
fees_columns = ['SENDER_CHANGE_FEE', 'HOLDING_FEES', 'TRANSFER_FEE', 'CREATE_FEE', 'LOCKING_FEE', 'BUY_MEMBER_TRAFFIC', 'PRE_APPROVAL_PURCHASE', 'SUBSCRIPTION_FEES']
possible_columns = rewards_columns + fees_columns
rewards_fees_columns = list(set(rewards_fees_columns) & set(possible_columns))
all_columns = ['consensus_time'] + rewards_fees_columns

rewards_fees = balance_reasons.select(all_columns)
rewards_fees = rewards_fees.group_by_dynamic(index_column='consensus_time', every='1d').agg(pl.all().sum())
df_fees = rewards_fees.select(['consensus_time'] + list(set(fees_columns) & set(rewards_fees_columns)))#'SENDER_CHANGE_FEE', 'HOLDING_FEES', 'TRANSFER_FEE', 'CREATE_FEE', 'LOCKING_FEE')
df_rewards = rewards_fees.select(['consensus_time'] + list(set(rewards_columns) & set(rewards_fees_columns)))#'SUPER_VALIDATOR_REWARD', 'VALIDATOR_LIVENESS', 'VALIDATOR_REWARD', 'UNFEATURED_APP_REWARD')

This cell creates a plot of the total rewards earned by the sample account over time.

In [159]:
plots = []
for column in list(set(rewards_columns) & set(rewards_fees_columns)):
        plots.append(go.Scatter(
            x=df_rewards['consensus_time'],
            y=df_rewards[column],
            mode='lines',
            name=column
        ))
fig_rewards = go.Figure(data=plots).update_layout(title_text='{}'.format(f"Total Rewards Earned by {sample}"))
fig_rewards

This cell creates a plot of the total fees paid by the sample account over time.

In [160]:
plots2 = []
for column2 in list(set(fees_columns) & set(rewards_fees_columns)):
    plots2.append(go.Scatter(
        x=df_fees['consensus_time'],
        y=df_fees[column2],
        mode='lines',
        name=column2
    ))
fig_fees = go.Figure(data=plots2).update_layout(title_text='{}'.format(f"Total Fees Paid by {sample}"))
fig_fees

This cell retrieves a list of all accounts for Canton Coin and calculates the total supply. It then calculates the percentage of the total supply held by each account.

In [179]:
df_accounts = client.get_list_of_accounts_v2(asset='cc', page_size=10000).to_list()
df_accounts = (pl.DataFrame(df_accounts).select('account', 'balance', 'n_debits', 'n_credits')
    .with_columns(
        pl.col('balance').cast(pl.Float64),
        pl.col('n_debits').cast(pl.Int64),
        pl.col('n_credits').cast(pl.Int64)
    )
    .sort(by='balance', descending=True)
    .with_columns((pl.col('n_debits') + pl.col('n_credits')).alias('total_balance_updates'))
              )
total_supply = df_accounts.filter(pl.col('account') == 'ISSUANCE')['balance'][0] * -1

df_accounts_1 = (df_accounts
    .filter(~pl.col('account').is_in(['ISSUANCE', 'FEES']))
    .with_columns((pl.col('balance')/total_supply*100).alias('pct_total_supply'))
              )
df_accounts_1.to_pandas()

account       balance  \
0    validator_validator_service_user::12206750ba8e...  5.327637e+09   
1    Cumberland-1::12201aa8a23046d5740c9edd58f7e820...  2.052036e+09   
2    Cumberland-2::1220120801da0994334c869a6db19d93...  2.049807e+09   
3    party-28dc4516-b5ca-44ff-86c7-2107e90a6807::12...  1.739779e+09   
4    Cumberland-Property-1::1220643de8d9bfdeb9187da...  1.714523e+09   
..                                                 ...           ...   
980  23d169c2-0909-4c70-81d1-1922de6febaa::12204afa...  0.000000e+00   
981  auth0_007c6823892690c95584e7025757::122001ec00...  0.000000e+00   
982  23d169c2-0909-4c70-81d1-1922de6febaa::12202196...  0.000000e+00   
983  cantonwallet::1220fd85022e5f0748e0e49ca8e0b226...  0.000000e+00   
984  23d169c2-0909-4c70-81d1-1922de6febaa::1220fac9...  0.000000e+00   

     n_debits  n_credits  total_balance_updates  pct_total_supply  
0       66961      90575                 157536         18.477368  
1       55387      55391                 110778          7.116894  
2       55382      55383                 110765          7.109163  
3     2231426    3441634                5673060          6.033919  
4      175981     223818                 399799          5.946326  
..        ...        ...                    ...               ...  
980         2          2                      4          0.000000  
981        20         32                     52          0.000000  
982         6         12                     18          0.000000  
983       367        368                    735          0.000000  
984         2          3                      5          0.000000  

[985 rows x 6 columns]

In [180]:
df_accounts_1 = df_accounts_1.with_columns(
    pl.col('account').str.split('::').list.get(0).alias('first_part'),
    pl.col('account').str.split('::').list.get(1).alias('second_part'),
)
df_accounts_1.to_pandas()

account       balance  \
0    validator_validator_service_user::12206750ba8e...  5.327637e+09   
1    Cumberland-1::12201aa8a23046d5740c9edd58f7e820...  2.052036e+09   
2    Cumberland-2::1220120801da0994334c869a6db19d93...  2.049807e+09   
3    party-28dc4516-b5ca-44ff-86c7-2107e90a6807::12...  1.739779e+09   
4    Cumberland-Property-1::1220643de8d9bfdeb9187da...  1.714523e+09   
..                                                 ...           ...   
980  23d169c2-0909-4c70-81d1-1922de6febaa::12204afa...  0.000000e+00   
981  auth0_007c6823892690c95584e7025757::122001ec00...  0.000000e+00   
982  23d169c2-0909-4c70-81d1-1922de6febaa::12202196...  0.000000e+00   
983  cantonwallet::1220fd85022e5f0748e0e49ca8e0b226...  0.000000e+00   
984  23d169c2-0909-4c70-81d1-1922de6febaa::1220fac9...  0.000000e+00   

     n_debits  n_credits  total_balance_updates  pct_total_supply  \
0       66961      90575                 157536         18.477368   
1       55387      55391                 110778          7.116894   
2       55382      55383                 110765          7.109163   
3     2231426    3441634                5673060          6.033919   
4      175981     223818                 399799          5.946326   
..        ...        ...                    ...               ...   
980         2          2                      4          0.000000   
981        20         32                     52          0.000000   
982         6         12                     18          0.000000   
983       367        368                    735          0.000000   
984         2          3                      5          0.000000   

                                     first_part  \
0              validator_validator_service_user   
1                                  Cumberland-1   
2                                  Cumberland-2   
3    party-28dc4516-b5ca-44ff-86c7-2107e90a6807   
4                         Cumberland-Property-1   
..                                          ...   
980        23d169c2-0909-4c70-81d1-1922de6febaa   
981          auth0_007c6823892690c95584e7025757   
982        23d169c2-0909-4c70-81d1-1922de6febaa   
983                                cantonwallet   
984        23d169c2-0909-4c70-81d1-1922de6febaa   

                                           second_part  
0    12206750ba8ed320d15bfed65ec62b0d3de6b954f05692...  
1    12201aa8a23046d5740c9edd58f7e820c83e7f5c58f255...  
2    1220120801da0994334c869a6db19d9321f3d5baf9e403...  
3    1220b8301e18aa8a401d6e34e6c20f8b0243183c514373...  
4    1220643de8d9bfdeb9187da2f770897fa50b34e17a39c0...  
..                                                 ...  
980  12204afac73fe9f866835bca61fdfd679fcdbb9511ea6c...  
981  122001ec00d642b30f6bf002a8079138b350f8ad34cb71...  
982  122021966adf518856575e47ad332322f800d4706dbb7c...  
983  1220fd85022e5f0748e0e49ca8e0b226307e71e1e25df3...  
984  1220fac9c51b2fa3f83da9ba509e1ac71037a01fe89fa6...  

[985 rows x 8 columns]

Let's shorten the account name a bit

In [183]:
df_accounts_2 = df_accounts_1.with_columns(
    (pl.col('first_part') + '::' +
    pl.col('second_part').str.slice(0, 4) +
    '..' +
    pl.col('second_part').str.slice(-4)).alias('account')
)
df_accounts_2.to_pandas()

account       balance  \
0         validator_validator_service_user::1220..7f0b  5.327637e+09   
1                             Cumberland-1::1220..0860  2.052036e+09   
2                             Cumberland-2::1220..ede6  2.049807e+09   
3    party-28dc4516-b5ca-44ff-86c7-2107e90a6807::12...  1.739779e+09   
4                    Cumberland-Property-1::1220..3c25  1.714523e+09   
..                                                 ...           ...   
980   23d169c2-0909-4c70-81d1-1922de6febaa::1220..ddc4  0.000000e+00   
981     auth0_007c6823892690c95584e7025757::1220..4273  0.000000e+00   
982   23d169c2-0909-4c70-81d1-1922de6febaa::1220..a466  0.000000e+00   
983                           cantonwallet::1220..a7b1  0.000000e+00   
984   23d169c2-0909-4c70-81d1-1922de6febaa::1220..5e16  0.000000e+00   

     n_debits  n_credits  total_balance_updates  pct_total_supply  \
0       66961      90575                 157536         18.477368   
1       55387      55391                 110778          7.116894   
2       55382      55383                 110765          7.109163   
3     2231426    3441634                5673060          6.033919   
4      175981     223818                 399799          5.946326   
..        ...        ...                    ...               ...   
980         2          2                      4          0.000000   
981        20         32                     52          0.000000   
982         6         12                     18          0.000000   
983       367        368                    735          0.000000   
984         2          3                      5          0.000000   

                                     first_part  \
0              validator_validator_service_user   
1                                  Cumberland-1   
2                                  Cumberland-2   
3    party-28dc4516-b5ca-44ff-86c7-2107e90a6807   
4                         Cumberland-Property-1   
..                                          ...   
980        23d169c2-0909-4c70-81d1-1922de6febaa   
981          auth0_007c6823892690c95584e7025757   
982        23d169c2-0909-4c70-81d1-1922de6febaa   
983                                cantonwallet   
984        23d169c2-0909-4c70-81d1-1922de6febaa   

                                           second_part  
0    12206750ba8ed320d15bfed65ec62b0d3de6b954f05692...  
1    12201aa8a23046d5740c9edd58f7e820c83e7f5c58f255...  
2    1220120801da0994334c869a6db19d9321f3d5baf9e403...  
3    1220b8301e18aa8a401d6e34e6c20f8b0243183c514373...  
4    1220643de8d9bfdeb9187da2f770897fa50b34e17a39c0...  
..                                                 ...  
980  12204afac73fe9f866835bca61fdfd679fcdbb9511ea6c...  
981  122001ec00d642b30f6bf002a8079138b350f8ad34cb71...  
982  122021966adf518856575e47ad332322f800d4706dbb7c...  
983  1220fd85022e5f0748e0e49ca8e0b226307e71e1e25df3...  
984  1220fac9c51b2fa3f83da9ba509e1ac71037a01fe89fa6...  

[985 rows x 8 columns]

This cell creates a pie chart of the percentage of total supply by account. It groups accounts with less than 5% of the total supply into an 'Other' category.

In [185]:
import plotly.express as px

threshold = 5

# Create a new dataframe with the 'other' category
df_pie = df_accounts_2.with_columns(
    pl.when(pl.col('pct_total_supply') < threshold)
    .then(pl.lit('Other'))
    .otherwise(pl.col('account'))
    .alias('account_group')
)

# Group by the new category and sum the percentages
df_pie = df_pie.group_by('account_group').agg(pl.sum('pct_total_supply').alias('pct_total_supply'))

# Create the pie chart
fig_pie = px.pie(df_pie, values='pct_total_supply', names='account_group', title='Percentage of Total Supply by Account')
fig_pie.show()

This cell fetches several supply-related metrics for Canton Coin and creates a line plot of them over time.

In [163]:
supply_metrics_df = client.get_asset_metrics(
    assets=['cc'],
    metrics=['SplyCur', 'SplyFF', 'SplyAct1d'],
    start_time="2025-05-01"
).to_dataframe()

df_melted = supply_metrics_df.melt(id_vars=['time', 'asset'], var_name='metric', value_name='value')

fig = px.line(
    df_melted,
    x='time',
    y='value',
    color='metric',
    title='Supply Metrics for Canton Coin'
)
fig.show()